# **Bitcoin price forecasting - RandomForestRegressor**
### Big Data Computing final project - A.Y. 2022 - 2023
Prof. Gabriele Tolomei

MSc in Computer Science

La Sapienza, University of Rome

### Author
Corsi Danilo - corsi.1742375@studenti.uniroma1.it



## Global constants, dependencies, libraries and tools

In [1]:
# GDrive root
GDRIVE_DIR = "/content/drive"

# Dataset
GDRIVE_DATASET_OUTPUT_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/datasets/output"
GDRIVE_DATASET_NAME = "bitcoin_blockchain_data_30min"
GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_NAME + "_train_valid"
GDRIVE_DATASET_NAME_EXT_ENG  = "/" + GDRIVE_DATASET_NAME_ENG + ".parquet"
GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_OUTPUT_DIR + GDRIVE_DATASET_NAME_EXT_ENG

# Features
GDRIVE_FEATURES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/features"
GDRIVE_ALL_FEATURES_NAME = "all_features"
GDRIVE_MORE_REL_FEATURES_NAME = "more_rel_features"
GDRIVE_LESS_REL_FEATURES_NAME = "less_rel_features"
GDRIVE_ALL_FEATURES_NAME_EXT = "/" + GDRIVE_ALL_FEATURES_NAME + ".json"
GDRIVE_MORE_REL_FEATURES_NAME_EXT = "/" + GDRIVE_MORE_REL_FEATURES_NAME + ".json"
GDRIVE_LESS_REL_FEATURES_NAME_EXT = "/" + GDRIVE_LESS_REL_FEATURES_NAME + ".json"
GDRIVE_ALL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_ALL_FEATURES_NAME_EXT
GDRIVE_MORE_REL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_MORE_REL_FEATURES_NAME_EXT
GDRIVE_LESS_REL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_LESS_REL_FEATURES_NAME_EXT

# Others
JAVA_HOME = "/usr/lib/jvm/java-8-openjdk-amd64"
MODEL_NAME = "RandomForestRegressor"
SLOW_OPERATION = True

In [2]:
# Point Colaboratory to our Google Drive
from google.colab import drive

# Define GDrive paths
drive.mount(GDRIVE_DIR, force_remount=True)

Mounted at /content/drive


In [3]:
import warnings

warnings.simplefilter(action='ignore', category=FutureWarning)

In [4]:
# Install Spark and related dependencies
!pip install pyspark

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 310.8/310.8 MB 4.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pyspark: filename=pyspark-3.4.1-py2.py3-none-any.whl size=311285388 sha256=dafd4a148c76045b05e89eb864d605274800ce77b61894c49b820c32ddd648a5
  Stored in directory: /root/.cache/pip/wheels/0d/77/a3/ff2f74cc9ab41f8f594dabf0579c2a7c6de920d584206e0834
Successfully built pyspark


## Import files

In [5]:
GDRIVE_UTILITIES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/utilities"

import sys
sys.path.append(GDRIVE_UTILITIES_DIR)

from imports import *
import utilities, parameters

importlib.reload(utilities)
importlib.reload(parameters)

<module 'parameters' from '/content/drive/MyDrive/BDC/project/utilities/parameters.py'>

## Create the pyspark session

In [6]:
# Create the session
conf = SparkConf().\
                set('spark.ui.port', "4050").\
                set('spark.executor.memory', '4G').\
                set('spark.driver.memory', '45G').\
                set('spark.driver.maxResultSize', '10G').\
                set("spark.kryoserializer.buffer.max", "1G").\
                setAppName("BitcoinPriceForecasting").\
                setMaster("local[*]")

# Create the context
sc = pyspark.SparkContext(conf=conf)
spark = SparkSession.builder.getOrCreate()

## Loading dataset

In [7]:
# Load datasets into pyspark dataset objects
df = spark.read.load(GDRIVE_DATASET_NAME_ENG,
                         format="parquet",
                         sep=",",
                         inferSchema="true",
                         header="true"
                    )

In [8]:
def dataset_info(dataset):
  dataset.show(3)

  # Get the number of rows
  num_rows = dataset.count()

  # Get the number of columns
  num_columns = len(dataset.columns)

  # Print the shape of the dataset
  print("Shape:", (num_rows, num_columns))

  # Print the schema of the dataset
  dataset.printSchema()

In [9]:
if SLOW_OPERATION:
  dataset_info(df)

+-------------------+---+------------------+--------------+-------------------+--------------+------------------+------------------+--------------------+------------------------+-----------------+-------------------+------------------+--------------------+------------------+------------------+--------------------------------+--------------------+------------------+------------------+------------------+------------------+------------------+------------------+
|          timestamp| id|      market-price|total-bitcoins|         market-cap|  trade-volume|       blocks-size|    avg-block-size|n-transactions-total|n-transactions-per-block|        hash-rate|         difficulty|    miners-revenue|transaction-fees-usd|n-unique-addresses|    n-transactions|estimated-transaction-volume-usd|      rate-of-change|        sma-5-days|        sma-7-days|       sma-10-days|       sma-20-days|       sma-50-days|      sma-100-days|
+-------------------+---+------------------+--------------+---------------

## Loading features

In [10]:
# Set the features label
FEATURES_LABEL = "features"

# Set the target variable
TARGET_VAL = 'market-price'

In [11]:
# Loading correlation matrix features
with open(GDRIVE_ALL_FEATURES, "r") as f:
    all_features = json.load(f)
print(all_features)

['total-bitcoins', 'market-cap', 'trade-volume', 'blocks-size', 'avg-block-size', 'n-transactions-total', 'n-transactions-per-block', 'hash-rate', 'difficulty', 'miners-revenue', 'transaction-fees-usd', 'n-unique-addresses', 'n-transactions', 'estimated-transaction-volume-usd', 'rate-of-change', 'sma-5-days', 'sma-7-days', 'sma-10-days', 'sma-20-days', 'sma-50-days', 'sma-100-days']


In [12]:
# Loading correlation matrix features
with open(GDRIVE_MORE_REL_FEATURES, "r") as f:
    more_rel_features = json.load(f)
print(more_rel_features)

['market-cap', 'miners-revenue', 'sma-5-days', 'sma-7-days', 'estimated-transaction-volume-usd', 'sma-10-days', 'n-transactions-total', 'blocks-size', 'sma-100-days', 'total-bitcoins']


In [13]:
# Loading correlation matrix features
with open(GDRIVE_LESS_REL_FEATURES, "r") as f:
    less_rel_features = json.load(f)
print(less_rel_features)

['sma-20-days', 'sma-50-days', 'n-unique-addresses', 'difficulty', 'hash-rate', 'avg-block-size', 'transaction-fees-usd', 'trade-volume', 'n-transactions-per-block', 'n-transactions', 'rate-of-change']


## Simple model

In [ ]:
# Get default params
params = parameters.get_defaults_model_params(MODEL_NAME)
params

{'numTrees': [20], 'maxDepth': [5]}

In [ ]:
# Valid performances with all the features
simple_res_all, simple_pred_all = utilities.evaluate_simple_model(df, all_features, params, GDRIVE_ALL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, False)
simple_res_all

Model    Type      Features Parameters         RMSE  \
0  RandomForestRegressor  simple  all_features    [20, 5]  2409.694757   

       MAPE          MAE      Variance        R2  Adjusted_R2      Time  
0  0.103372  2000.494009  3.529554e+06  0.365648     0.365399  5.088836

In [ ]:
utilities.show_results(simple_pred_all, MODEL_NAME, TARGET_VAL)

In [ ]:
# Valid performances with the corr matrix features
simple_res_more_rel, simple_pred_more_rel = utilities.evaluate_simple_model(df, more_rel_features, params, GDRIVE_MORE_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, False)
simple_res_more_rel

Model    Type           Features Parameters         RMSE  \
0  RandomForestRegressor  simple  more_rel_features    [20, 5]  2465.704829   

       MAPE          MAE      Variance        R2  Adjusted_R2      Time  
0  0.102436  1992.954121  1.818824e+06  0.335816     0.335555  5.556753

In [ ]:
utilities.show_results(simple_pred_more_rel, MODEL_NAME, TARGET_VAL)

In [ ]:
# Valid performances with the corr matrix features
simple_res_less_rel, simple_pred_less_rel = utilities.evaluate_simple_model(df, less_rel_features, params, GDRIVE_LESS_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, False)
simple_res_less_rel

Model    Type           Features Parameters          RMSE  \
0  RandomForestRegressor  simple  less_rel_features    [20, 5]  15726.784482   

       MAPE           MAE      Variance         R2  Adjusted_R2     Time  
0  0.729469  14454.621469  2.446057e+08 -26.020038   -26.030673  4.69045

In [ ]:
utilities.show_results(simple_pred_less_rel, MODEL_NAME, TARGET_VAL)

## Simple model (with data normalization)

In [ ]:
# Valid performances with all the features
simple_norm_res_all, simple_norm_pred_all = utilities.evaluate_simple_model(df, all_features, params, GDRIVE_ALL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, True)
simple_norm_res_all

Model         Type      Features Parameters         RMSE  \
0  RandomForestRegressor  simple_norm  all_features    [20, 5]  4071.172784   

       MAPE          MAE      Variance        R2  Adjusted_R2     Time  
0  0.147115  3208.071048  7.400315e+06 -0.810694     -0.81155  6.21642

In [ ]:
utilities.show_results(simple_norm_pred_all, MODEL_NAME, TARGET_VAL)

In [ ]:
# Valid performances with the corr matrix features
simple_norm_res_more_rel, simple_norm_pred_more_rel = utilities.evaluate_simple_model(df, more_rel_features, params, GDRIVE_MORE_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, True)
simple_norm_res_more_rel

Model         Type           Features Parameters  \
0  RandomForestRegressor  simple_norm  more_rel_features    [20, 5]   

          RMSE      MAPE          MAE      Variance        R2  Adjusted_R2  \
0  2324.655826  0.080447  1705.924394  1.023073e+07  0.409631     0.409352   

       Time  
0  6.112795

In [ ]:
utilities.show_results(simple_norm_pred_more_rel, MODEL_NAME, TARGET_VAL)

In [ ]:
# Valid performances with the corr matrix features
simple_norm_res_less_rel, simple_norm_pred_less_rel = utilities.evaluate_simple_model(df, less_rel_features, params, GDRIVE_LESS_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, True)
simple_norm_res_less_rel

Model         Type           Features Parameters  \
0  RandomForestRegressor  simple_norm  less_rel_features    [20, 5]   

           RMSE      MAPE           MAE      Variance         R2  Adjusted_R2  \
0  13526.942657  0.667781  13197.483421  1.772172e+08 -18.989659   -18.999101   

       Time  
0  4.909864

In [ ]:
utilities.show_results(simple_norm_pred_less_rel, MODEL_NAME, TARGET_VAL)

## Hyperparameter tuning

In [ ]:
choosen_features = all_features
CHOSEN_FEATURES_LABEL = GDRIVE_ALL_FEATURES_NAME

In [ ]:
# Split proportion list
PORTION_LIST = [0.6, 0.7, 0.8, 0.9]

In [ ]:
# Get simple params
params = parameters.get_model_params(MODEL_NAME)
params

{'numTrees': [10, 20, 30], 'maxDepth': [3, 5, 8]}

In [ ]:
hyp_res, hyp_params = utilities.autoTuning(df, choosen_features, params, CHOSEN_FEATURES_LABEL, PORTION_LIST, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
hyp_res

Model        Type      Features  Proportion Parameters  \
0  RandomForestRegressor  autotuning  all_features         0.9    [20, 5]   

          RMSE      MAPE          MAE      Variance        R2  Adjusted_R2  \
0  4071.172784  0.147115  3208.071048  7.400315e+06 -0.810694     -0.81155   

       Time  
0  3.771292

## Cross validation

In [ ]:
# Get tuned params
params = hyp_params
params

{'numTrees': [20], 'maxDepth': [5]}

In [ ]:
## Cross Validation Parameter
# Multiple Splits Time Series Cross Validation
mul_cv = {'cv_type':'mulTs',
          'kSplits': 5}

# Blocked Time Series Cross Validation
blk_cv = {'cv_type':'blkTs',
          'kSplits': 10}

In [ ]:
mul_cv_res, trained_models_mul_cv = utilities.tsCrossValidation(df, choosen_features, params, mul_cv, CHOSEN_FEATURES_LABEL, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
mul_cv_res

Model   Type      Features  Splits Train&Validation  \
0  RandomForestRegressor  mulTs  all_features       1   (21182, 21181)   
1  RandomForestRegressor  mulTs  all_features       2   (42363, 21181)   
2  RandomForestRegressor  mulTs  all_features       3   (63544, 21181)   
3  RandomForestRegressor  mulTs  all_features       4   (84725, 21181)   
4  RandomForestRegressor  mulTs  all_features       5  (105906, 21181)   

  Parameters          RMSE      MAPE           MAE      Variance        R2  \
0    [20, 5]   6673.817781  0.669715   5175.369044  2.671137e+07 -1.497084   
1    [20, 5]   2771.262617  0.490581   2389.804778  2.621676e+06 -0.449406   
2    [20, 5]   3576.820486  0.326839   3142.878942  1.112398e+07 -4.041063   
3    [20, 5]  37033.894543  0.752644  34327.948310  1.179012e+09 -6.743702   
4    [20, 5]   5961.138928  0.210481   4904.534585  1.027116e+08  0.572099   

   Adjusted_R2      Time  
0    -1.497792  4.342702  
1    -0.449817  3.097295  
2    -4.042491  3.790078  
3    -6.745896  4.285516  
4     0.571977  4.833847

In [ ]:
blk_cv_res, trained_models_mul_cv = utilities.tsCrossValidation(df, choosen_features, params, blk_cv, CHOSEN_FEATURES_LABEL, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
blk_cv_res

Model   Type      Features  Splits Train&Validation  \
0  RandomForestRegressor  blkTs  all_features       1    (10166, 2542)   
1  RandomForestRegressor  blkTs  all_features       2    (10166, 2542)   
2  RandomForestRegressor  blkTs  all_features       3    (10166, 2542)   
3  RandomForestRegressor  blkTs  all_features       4    (10166, 2542)   
4  RandomForestRegressor  blkTs  all_features       5    (10166, 2542)   
5  RandomForestRegressor  blkTs  all_features       6    (10166, 2542)   
6  RandomForestRegressor  blkTs  all_features       7    (10166, 2542)   
7  RandomForestRegressor  blkTs  all_features       8    (10166, 2542)   
8  RandomForestRegressor  blkTs  all_features       9    (10166, 2542)   
9  RandomForestRegressor  blkTs  all_features      10    (10166, 2542)   

  Parameters          RMSE      MAPE           MAE      Variance        R2  \
0    [20, 5]     50.425002  0.072998     43.021214  2.934778e+03 -5.905500   
1    [20, 5]    891.883982  0.330416    732.494495  5.368999e+05 -1.942218   
2    [20, 5]   3630.783298  0.323621   3425.584697  1.417706e+07 -4.306698   
3    [20, 5]    732.186537  0.077989    398.725718  1.398535e+05 -0.425427   
4    [20, 5]   1860.142068  0.152913   1695.062374  3.376587e+06 -4.152492   
5    [20, 5]    908.689600  0.121832    818.613687  5.840869e+05  0.111179   
6    [20, 5]  12684.902867  0.332736  10645.974688  1.136448e+08 -2.304958   
7    [20, 5]   8139.375650  0.150457   7439.773725  8.221471e+07 -1.263463   
8    [20, 5]   9201.304193  0.344799   7348.482506  5.561161e+07 -2.977728   
9    [20, 5]   3105.836297  0.105807   2643.174340  1.045239e+07 -0.703686   

   Adjusted_R2      Time  
0    -5.921845  2.025715  
1    -1.949181  1.988070  
2    -4.319258  2.060881  
3    -0.428801  2.987668  
4    -4.164687  1.910017  
5     0.109075  1.935184  
6    -2.312780  2.257036  
7    -1.268820  3.280749  
8    -2.987143  2.026836  
9    -0.707719  2.006859

## Comparison table

In [ ]:
# Define what model_info and evaluators in the Model Comparison Table
model_info = ['Model','Type', 'Features', 'Parameters']
evaluator_lst = ['RMSE','MAPE','MAE','Variance','R2','Adjusted_R2','Time']

# The the Cross Validation results would like to compare
comparison_lst = [simple_res_all, simple_res_more_rel, simple_res_less_rel, simple_norm_res_all, simple_norm_res_more_rel, simple_norm_res_less_rel, hyp_res, mul_cv_res, blk_cv_res]

In [ ]:
# Show the Comparison Table
pd.concat([utilities.modelComparison(cv_result, model_info, evaluator_lst) for cv_result in comparison_lst])

Model         Type           Features Parameters  \
0  RandomForestRegressor       simple       all_features    [20, 5]   
0  RandomForestRegressor       simple  more_rel_features    [20, 5]   
0  RandomForestRegressor       simple  less_rel_features    [20, 5]   
0  RandomForestRegressor  simple_norm       all_features    [20, 5]   
0  RandomForestRegressor  simple_norm  more_rel_features    [20, 5]   
0  RandomForestRegressor  simple_norm  less_rel_features    [20, 5]   
0  RandomForestRegressor   autotuning       all_features    [20, 5]   
0  RandomForestRegressor        mulTs       all_features    [20, 5]   
0  RandomForestRegressor        blkTs       all_features    [20, 5]   

           RMSE      MAPE           MAE      Variance         R2  Adjusted_R2  \
0   2409.694757  0.103372   2000.494009  3.529554e+06   0.365648     0.365399   
0   2465.704829  0.102436   1992.954121  1.818824e+06   0.335816     0.335555   
0  15726.784482  0.729469  14454.621469  2.446057e+08 -26.020038   -26.030673   
0   4071.172784  0.147115   3208.071048  7.400315e+06  -0.810694    -0.811550   
0   2324.655826  0.080447   1705.924394  1.023073e+07   0.409631     0.409352   
0  13526.942657  0.667781  13197.483421  1.772172e+08 -18.989659   -18.999101   
0   4071.172784  0.147115   3208.071048  7.400315e+06  -0.810694    -0.811550   
0  11203.386871  0.490052   9988.107132  2.644361e+08  -2.431831    -2.432804   
0   4120.552949  0.201357   3519.090744  2.807410e+07  -2.387099    -2.395116   

       Time  
0  5.088836  
0  5.556753  
0  4.690450  
0  6.216420  
0  6.112795  
0  4.909864  
0  3.771292  
0  4.069888  
0  2.247901

## Training the final model

In [16]:
model = utilities.train_final_model(df, choosen_features, params, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)

In [17]:
GDRIVE_MODELS_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/models"
GDRIVE_MODEL_NAME_EXT = GDRIVE_MODELS_DIR + "/" + MODEL_NAME

In [18]:
# Save the trained model
model.write().overwrite().save(GDRIVE_MODEL_NAME_EXT)